In [20]:
from ngsolve import *
from netgen.geom2d import SplineGeometry
from math import pi
geo = SplineGeometry()
points     = [ (0, 0), (1, 0),  (1, 0.5), (1, 1), (0, 1), (0, 0.5)]
pnums    = [geo.AppendPoint(*pt) for pt in points]
l1 = geo.Append(["line", 0, 1], leftdomain=2, rightdomain=0, bc="GammaD")
l2 = geo.Append(["line", 1, 2], leftdomain=2, rightdomain=0, bc="GammaD")
l3 = geo.Append(["line", 2, 3], leftdomain=1, rightdomain=0, bc="GammaS")
l4 = geo.Append(["line", 3, 4], leftdomain=1, rightdomain=0, bc="GammaS")
l5 = geo.Append(["line", 4, 5], leftdomain=1, rightdomain=0, bc="GammaS")
l6 = geo.Append(["line", 5, 0], leftdomain=2, rightdomain=0, bc="GammaD")
l7 = geo.Append(["line", 5, 2], leftdomain=1, rightdomain=2, bc="GammaI")

geo.SetMaterial(1, "stokesregion")
geo.SetMaterial(2, "darcyregion")
mesh = Mesh( geo.GenerateMesh(maxh=0.2) )

Draw(mesh)
mesh.nv, mesh.ne


fD=CoefficientFunction((1/(2*pi)-2*pi)*cos(pi*x)*exp(y/2))

k = 2
V = VectorL2(mesh,order=k)
Q = L2(mesh,order=k-1)
Vbar  = FacetFESpace(mesh, order = k, dirichlet= "GammaS", definedon = mesh.Materials("stokesregion"))
QbarS = FacetFESpace(mesh, order = k, definedon=mesh.Materials("stokesregion"))
QbarD = FacetFESpace(mesh, order = k, definedon=mesh.Materials("darcyregion"))
R = NumberSpace(mesh)

X = FESpace([V, Vbar, Vbar, Q, QbarS, QbarD, R])


(u, ubar1, ubar2, p, pbarS, pbarD, lam1)  = X.TrialFunction()
(v, vbar1, vbar2, q, qbarS, qbarD, lam2)  = X.TestFunction()

#L2 projection of fD on Q
gfu = GridFunction(Q)

a = BilinearForm(X)
a += gfu*q*dx
a.Assemble()

f  = LinearForm(X)
f += fD*q*dx
f.Assemble()

#Solve
inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")
res = f.vec.CreateVector()
res.data = f.vec - a.mat*gfu.vec
gfu.vec.data += inv * res


print("L2projection", gfu.vec)




NgException: UmfpackInverse: Numeric factorization failed.